# 1. Import library
Note: Combined from various sources, much more comprehensive than the original code provided. Import 也很讲究 XDXD

Also note: For this "Ab_Virus_02_Model_Selection_v01.ipynb" Jupyter Notebook, you can switch back to your normal pip3 or conda environment.

### 1.1 Import OS and Path

In [1]:
import os
from pathlib import Path

### 1.2 Import data structures

In [2]:
import numpy as np
from numpy import arange, logspace
import pandas as pd
import multiprocessing
import logging
import csv
import json

### 1.3 Import visualisation tools

In [3]:
import seaborn as sb
sb.set()
from matplotlib import pyplot
import matplotlib.pyplot as plt
%matplotlib inline

### 1.4 Import Scikit Learn - data analytics

In [4]:
# The code for featurization was borrowed from deepchem. Please refer https://deepchem.io for more information
from scipy import stats
from scipy.stats import randint, uniform
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV, RandomizedSearchCV, KFold, cross_val_score, StratifiedKFold, RepeatedStratifiedKFold
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score, roc_auc_score, average_precision_score, mean_squared_error, r2_score, precision_score,recall_score, f1_score
from sklearn.model_selection import cross_val_score

### 1.5 Import Scikit Learn - classifiers

In [5]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression, Lasso
from sklearn import svm
from sklearn.svm import LinearSVC
from sklearn.neural_network import MLPClassifier

### 1.5 Import XGBoost

In [6]:
import xgboost as xgb
from xgboost.sklearn import XGBClassifier
from xgboost import plot_importance
from xgboost import plot_importance

### 1.6 Import other classifiers

In [7]:
import lightgbm as lgb
from lightgbm import LGBMClassifier
import catboost as cb
from catboost import CatBoostClassifier

### 1.7 Import Pytorch Tabnet

In [8]:
import torch
from pytorch_tabnet.tab_model import TabNetClassifier
from pytorch_tabular import TabularModel
from pytorch_tabular.models import CategoryEmbeddingModelConfig
from pytorch_tabular.config import DataConfig, OptimizerConfig, TrainerConfig, ExperimentConfig

# 2. Data structures loading and preparation

### 2.1 Load NumPy files from directory

In [9]:
CURRENT_PATH = os.getcwd()
print(CURRENT_PATH)

mean_final_elementwise_sum = np.load(os.path.join(os.getcwd(), "mean_final_elementwise_sum.npy"))
print("Loaded file 'mean_final_elementwise_sum.npy'")

mean_final_concatenate = np.load(os.path.join(os.getcwd(), "mean_final_concatenate.npy"))
print("Loaded file 'mean_final_concatenate.npy'")

IC50_class = np.load(os.path.join(os.getcwd(), "IC50_class.npy"))
print("Loaded file 'IC50_class.npy'")

print(mean_final_elementwise_sum.shape)
print(mean_final_concatenate.shape)
print(IC50_class.shape)

/Users/Joshua/Dropbox/NTU_studies/2021_22_Year_2/URECA/Reading/PotentialAB
Loaded file 'mean_final_elementwise_sum.npy'
Loaded file 'mean_final_concatenate.npy'
Loaded file 'IC50_class.npy'
(1933, 37)
(1933, 74)
(1933,)


### 2.2 CSV file preparation

In [10]:
csv_file_name = "Ab_Virus_02_Model_Selection_v03.csv"
print(csv_file_name)

Ab_Virus_02_Model_Selection_v03.csv


# 3. Model 1: Random Forest Classifier

### 3.1 Apply Random Forest Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [11]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [12]:
# Apply Random Forest Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # Random Forest Classifier
    rf = RandomForestClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    rf.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = rf.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 96.12%
ROC AUC score: 94.59%
RepeatedStratifiedKFold = 2
Accuracy: 95.61%
ROC AUC score: 93.54%
RepeatedStratifiedKFold = 3
Accuracy: 96.90%
ROC AUC score: 95.10%
RepeatedStratifiedKFold = 4
Accuracy: 93.52%
ROC AUC score: 90.74%
RepeatedStratifiedKFold = 5
Accuracy: 95.34%
ROC AUC score: 94.39%
RepeatedStratifiedKFold = 6
Accuracy: 95.87%
ROC AUC score: 93.71%
RepeatedStratifiedKFold = 7
Accuracy: 95.09%
ROC AUC score: 92.13%
RepeatedStratifiedKFold = 8
Accuracy: 95.09%
ROC AUC score: 93.20%
RepeatedStratifiedKFold = 9
Accuracy: 95.34%
ROC AUC score: 93.72%
RepeatedStratifiedKFold = 10
Accuracy: 97.15%
ROC AUC score: 97.03%
RepeatedStratifiedKFold = 11
Accuracy: 95.87%
ROC AUC score: 94.77%
RepeatedStratifiedKFold = 12
Accuracy: 95.61%
ROC AUC score: 94.60%
RepeatedStratifiedKFold = 13
Accuracy: 95.61%
ROC AUC score: 93.89%
RepeatedStratifiedKFold = 14
Accuracy: 95.85%
ROC AUC score: 92.64%
RepeatedStratifiedKFold = 15
Accuracy: 96.37%
ROC AUC sco

### 3.2 Printing Accuracy score and ROC AUC score

In [13]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([96.12, 95.61, 96.9 , 93.52, 95.34, 95.87, 95.09, 95.09, 95.34,
       97.15, 95.87, 95.61, 95.61, 95.85, 96.37, 94.83, 94.83, 96.9 ,
       95.08, 95.34, 95.87, 95.87, 94.83, 94.82, 96.63, 94.06, 95.87,
       96.64, 95.34, 95.85, 97.67, 95.61, 94.83, 95.6 , 95.6 , 93.54,
       96.9 , 95.87, 96.63, 96.11, 95.61, 95.09, 96.9 , 95.6 , 94.56,
       95.61, 95.87, 96.12, 95.08, 96.63])
Mean   | Max    | Min
95.67% | 97.67% | 93.52%
ROC AUC score array: array([94.59, 93.54, 95.1 , 90.74, 94.39, 93.71, 92.13, 93.2 , 93.72,
       97.03, 94.77, 94.6 , 93.89, 92.64, 94.72, 92.31, 93.02, 95.1 ,
       92.84, 93.67, 94.42, 94.42, 93.73, 93.37, 94.53, 92.16, 94.77,
       94.22, 93.72, 94.37, 96.68, 93.89, 92.31, 93.18, 94.2 , 91.81,
       95.81, 93.35, 95.28, 94.55, 94.25, 92.84, 96.17, 94.24, 91.72,
       94.25, 93.35, 94.59, 93.9 , 94.53])
Mean   | Max    | Min
93.93% | 97.03% | 90.74%


### 3.3 Storing into csv

In [14]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['random forest', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['random forest', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 3.4 Apply Random Forest Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_concatenate

In [15]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [16]:
# Apply Random Forest Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # Random Forest Classifier
    rf = RandomForestClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    rf.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = rf.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 95.87%
ROC AUC score: 94.42%
RepeatedStratifiedKFold = 2
Accuracy: 96.12%
ROC AUC score: 94.59%
RepeatedStratifiedKFold = 3
Accuracy: 97.16%
ROC AUC score: 95.63%
RepeatedStratifiedKFold = 4
Accuracy: 94.04%
ROC AUC score: 91.79%
RepeatedStratifiedKFold = 5
Accuracy: 95.60%
ROC AUC score: 94.56%
RepeatedStratifiedKFold = 6
Accuracy: 96.64%
ROC AUC score: 94.93%
RepeatedStratifiedKFold = 7
Accuracy: 95.35%
ROC AUC score: 92.66%
RepeatedStratifiedKFold = 8
Accuracy: 95.09%
ROC AUC score: 93.55%
RepeatedStratifiedKFold = 9
Accuracy: 96.37%
ROC AUC score: 95.47%
RepeatedStratifiedKFold = 10
Accuracy: 97.15%
ROC AUC score: 97.03%
RepeatedStratifiedKFold = 11
Accuracy: 96.38%
ROC AUC score: 95.83%
RepeatedStratifiedKFold = 12
Accuracy: 96.12%
ROC AUC score: 95.66%
RepeatedStratifiedKFold = 13
Accuracy: 95.61%
ROC AUC score: 94.25%
RepeatedStratifiedKFold = 14
Accuracy: 95.85%
ROC AUC score: 93.00%
RepeatedStratifiedKFold = 15
Accuracy: 96.63%
ROC AUC sco

In [17]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([95.87, 96.12, 97.16, 94.04, 95.6 , 96.64, 95.35, 95.09, 96.37,
       97.15, 96.38, 96.12, 95.61, 95.85, 96.63, 95.61, 95.61, 97.16,
       95.34, 95.34, 96.12, 96.38, 95.35, 95.34, 96.63, 94.83, 95.61,
       97.42, 95.6 , 95.85, 97.42, 96.12, 95.09, 95.85, 96.11, 94.06,
       97.16, 96.12, 96.89, 95.34, 96.12, 95.35, 97.42, 96.37, 94.56,
       95.87, 96.38, 96.38, 95.6 , 96.89])
Mean   | Max    | Min
95.99% | 97.42% | 94.04%
ROC AUC score array: array([94.42, 94.59, 95.63, 91.79, 94.56, 94.93, 92.66, 93.55, 95.47,
       97.03, 95.83, 95.66, 94.25, 93.  , 94.89, 93.54, 94.6 , 95.63,
       93.01, 93.67, 94.59, 95.47, 94.43, 94.43, 94.53, 93.02, 94.6 ,
       95.8 , 94.24, 94.37, 96.51, 94.95, 92.49, 93.71, 95.27, 92.87,
       95.99, 93.88, 95.81, 92.95, 94.95, 93.37, 96.87, 95.82, 91.72,
       94.42, 94.76, 95.12, 94.95, 95.06])
Mean   | Max    | Min
94.51% | 97.03% | 91.72%


In [18]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['random forest', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['random forest', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

# 4. Model 2: Decision Tree Classifier

### 4.1 Apply Decision Tree Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [19]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [20]:
# Apply Decision Tree Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # Decision Tree Classifier
    dectree = DecisionTreeClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    dectree.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = dectree.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 93.80%
ROC AUC score: 92.34%
RepeatedStratifiedKFold = 2
Accuracy: 95.35%
ROC AUC score: 93.72%
RepeatedStratifiedKFold = 3
Accuracy: 96.64%
ROC AUC score: 94.93%
RepeatedStratifiedKFold = 4
Accuracy: 92.23%
ROC AUC score: 89.53%
RepeatedStratifiedKFold = 5
Accuracy: 94.56%
ROC AUC score: 93.52%
RepeatedStratifiedKFold = 6
Accuracy: 95.61%
ROC AUC score: 93.18%
RepeatedStratifiedKFold = 7
Accuracy: 94.57%
ROC AUC score: 91.43%
RepeatedStratifiedKFold = 8
Accuracy: 95.09%
ROC AUC score: 93.55%
RepeatedStratifiedKFold = 9
Accuracy: 95.60%
ROC AUC score: 94.95%
RepeatedStratifiedKFold = 10
Accuracy: 94.82%
ROC AUC score: 93.33%
RepeatedStratifiedKFold = 11
Accuracy: 95.61%
ROC AUC score: 95.31%
RepeatedStratifiedKFold = 12
Accuracy: 93.80%
ROC AUC score: 92.34%
RepeatedStratifiedKFold = 13
Accuracy: 94.32%
ROC AUC score: 93.04%
RepeatedStratifiedKFold = 14
Accuracy: 94.82%
ROC AUC score: 91.60%
RepeatedStratifiedKFold = 15
Accuracy: 94.56%
ROC AUC sco

In [21]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([93.8 , 95.35, 96.64, 92.23, 94.56, 95.61, 94.57, 95.09, 95.6 ,
       94.82, 95.61, 93.8 , 94.32, 94.82, 94.56, 94.57, 94.32, 96.12,
       95.08, 94.3 , 95.61, 95.35, 93.02, 94.3 , 95.85, 94.06, 95.09,
       96.38, 94.82, 94.82, 97.16, 94.32, 93.8 , 94.04, 95.85, 93.02,
       96.12, 95.61, 94.56, 95.6 , 95.09, 93.54, 97.16, 95.08, 93.78,
       94.57, 95.09, 95.09, 94.04, 95.34])
Mean   | Max    | Min
94.88% | 97.16% | 92.23%
ROC AUC score array: array([92.34, 93.72, 94.93, 89.53, 93.52, 93.18, 91.43, 93.55, 94.95,
       93.33, 95.31, 92.34, 93.04, 91.6 , 92.8 , 91.79, 92.33, 94.24,
       93.19, 92.63, 94.25, 94.43, 92.18, 92.32, 94.01, 92.16, 94.26,
       94.76, 93.37, 92.61, 96.34, 92.33, 91.63, 91.44, 95.1 , 91.12,
       95.3 , 93.54, 91.78, 94.2 , 93.91, 92.17, 96.7 , 94.25, 90.12,
       93.56, 92.49, 94.26, 92.5 , 92.95])
Mean   | Max    | Min
93.20% | 96.70% | 89.53%


In [22]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['decision tree', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['decision tree', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 4.2 Apply Decision Tree Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_concatenate

In [23]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [24]:
# Apply Decision Tree Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # Decision Tree Classifier
    dectree = DecisionTreeClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    dectree.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = dectree.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 95.61%
ROC AUC score: 94.25%
RepeatedStratifiedKFold = 2
Accuracy: 95.61%
ROC AUC score: 94.25%
RepeatedStratifiedKFold = 3
Accuracy: 96.64%
ROC AUC score: 94.93%
RepeatedStratifiedKFold = 4
Accuracy: 94.04%
ROC AUC score: 91.79%
RepeatedStratifiedKFold = 5
Accuracy: 95.08%
ROC AUC score: 93.50%
RepeatedStratifiedKFold = 6
Accuracy: 95.35%
ROC AUC score: 93.01%
RepeatedStratifiedKFold = 7
Accuracy: 95.09%
ROC AUC score: 91.78%
RepeatedStratifiedKFold = 8
Accuracy: 95.09%
ROC AUC score: 93.55%
RepeatedStratifiedKFold = 9
Accuracy: 95.85%
ROC AUC score: 94.77%
RepeatedStratifiedKFold = 10
Accuracy: 94.30%
ROC AUC score: 92.99%
RepeatedStratifiedKFold = 11
Accuracy: 95.35%
ROC AUC score: 94.43%
RepeatedStratifiedKFold = 12
Accuracy: 94.57%
ROC AUC score: 92.85%
RepeatedStratifiedKFold = 13
Accuracy: 95.61%
ROC AUC score: 94.25%
RepeatedStratifiedKFold = 14
Accuracy: 95.60%
ROC AUC score: 92.83%
RepeatedStratifiedKFold = 15
Accuracy: 95.34%
ROC AUC sco

In [25]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([95.61, 95.61, 96.64, 94.04, 95.08, 95.35, 95.09, 95.09, 95.85,
       94.3 , 95.35, 94.57, 95.61, 95.6 , 95.34, 94.83, 95.09, 96.12,
       94.82, 94.82, 96.12, 95.87, 95.35, 94.56, 96.11, 94.32, 95.09,
       96.9 , 95.08, 94.56, 96.9 , 94.83, 95.09, 95.08, 95.6 , 94.06,
       96.64, 95.61, 94.82, 95.34, 95.09, 94.32, 97.16, 95.08, 94.56,
       95.87, 96.38, 95.35, 94.3 , 95.85])
Mean   | Max    | Min
95.33% | 97.16% | 94.04%
ROC AUC score array: array([94.25, 94.25, 94.93, 91.79, 93.5 , 93.01, 91.78, 93.55, 94.77,
       92.99, 94.43, 92.85, 94.25, 92.83, 93.67, 91.96, 93.55, 94.95,
       92.66, 94.05, 94.95, 94.42, 94.08, 93.2 , 93.82, 92.68, 94.26,
       95.1 , 93.54, 92.8 , 96.17, 93.38, 92.49, 93.19, 94.92, 93.22,
       95.64, 93.89, 92.31, 93.31, 93.55, 91.97, 96.7 , 93.9 , 91.72,
       94.77, 94.41, 94.08, 93.03, 93.29])
Mean   | Max    | Min
93.70% | 96.70% | 91.72%


In [26]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['decision tree', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['decision tree', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

# 5. Model 3: Logistic Regression

### 5.1 Apply Logistic Regression with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [27]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [28]:
# Apply Logistic Regression with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # Logistic Regression
    LR = LogisticRegression(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    LR.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = LR.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 87.60%
ROC AUC score: 76.87%
RepeatedStratifiedKFold = 2
Accuracy: 86.82%
ROC AUC score: 73.51%
RepeatedStratifiedKFold = 3
Accuracy: 88.11%
ROC AUC score: 77.21%
RepeatedStratifiedKFold = 4
Accuracy: 85.75%
ROC AUC score: 73.18%
RepeatedStratifiedKFold = 5
Accuracy: 87.31%
ROC AUC score: 76.82%
RepeatedStratifiedKFold = 6
Accuracy: 88.63%
ROC AUC score: 77.91%
RepeatedStratifiedKFold = 7
Accuracy: 84.24%
ROC AUC score: 68.60%
RepeatedStratifiedKFold = 8
Accuracy: 88.37%
ROC AUC score: 78.80%
RepeatedStratifiedKFold = 9
Accuracy: 86.27%
ROC AUC score: 74.23%
RepeatedStratifiedKFold = 10
Accuracy: 88.60%
ROC AUC score: 78.76%
RepeatedStratifiedKFold = 11
Accuracy: 86.56%
ROC AUC score: 74.76%
RepeatedStratifiedKFold = 12
Accuracy: 89.15%
ROC AUC score: 80.74%
RepeatedStratifiedKFold = 13
Accuracy: 83.72%
ROC AUC score: 67.91%
RepeatedStratifiedKFold = 14
Accuracy: 85.49%
ROC AUC score: 70.88%
RepeatedStratifiedKFold = 15
Accuracy: 87.56%
ROC AUC sco

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Accuracy: 85.23%
ROC AUC score: 70.71%
RepeatedStratifiedKFold = 20
Accuracy: 87.31%
ROC AUC score: 76.82%
RepeatedStratifiedKFold = 21
Accuracy: 88.11%
ROC AUC score: 77.21%
RepeatedStratifiedKFold = 22
Accuracy: 87.86%
ROC AUC score: 77.39%
RepeatedStratifiedKFold = 23
Accuracy: 87.08%
ROC AUC score: 75.81%
RepeatedStratifiedKFold = 24
Accuracy: 87.82%
ROC AUC score: 76.68%
RepeatedStratifiedKFold = 25
Accuracy: 85.75%
ROC AUC score: 72.55%
RepeatedStratifiedKFold = 26
Accuracy: 84.75%
ROC AUC score: 70.01%
RepeatedStratifiedKFold = 27
Accuracy: 87.08%
ROC AUC score: 75.10%
RepeatedStratifiedKFold = 28
Accuracy: 87.86%
ROC AUC score: 76.33%
RepeatedStratifiedKFold = 29
Accuracy: 87.31%
ROC AUC score: 77.76%
RepeatedStratifiedKFold = 30
Accuracy: 88.08%
ROC AUC score: 76.97%
RepeatedStratifiedKFold = 31
Accuracy: 87.60%
ROC AUC score: 74.74%
RepeatedStratifiedKFold = 32
Accuracy: 88.11%
ROC AUC score: 77.56%
RepeatedStratifiedKFold = 33
Accuracy: 85.01%
ROC AUC score: 71.96%
RepeatedS

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Accuracy: 86.53%
ROC AUC score: 74.40%
RepeatedStratifiedKFold = 40
Accuracy: 87.05%
ROC AUC score: 74.85%
RepeatedStratifiedKFold = 41
Accuracy: 87.08%
ROC AUC score: 75.46%
RepeatedStratifiedKFold = 42
Accuracy: 86.05%
ROC AUC score: 73.35%
RepeatedStratifiedKFold = 43
Accuracy: 85.53%
ROC AUC score: 70.53%
RepeatedStratifiedKFold = 44
Accuracy: 88.60%
ROC AUC score: 78.97%
RepeatedStratifiedKFold = 45
Accuracy: 88.34%
ROC AUC score: 77.87%
RepeatedStratifiedKFold = 46
Accuracy: 87.60%
ROC AUC score: 76.51%
RepeatedStratifiedKFold = 47
Accuracy: 85.79%
ROC AUC score: 71.41%
RepeatedStratifiedKFold = 48
Accuracy: 87.34%
ROC AUC score: 76.70%
RepeatedStratifiedKFold = 49
Accuracy: 87.82%
ROC AUC score: 78.10%
RepeatedStratifiedKFold = 50
Accuracy: 86.79%
ROC AUC score: 74.68%


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [29]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([87.6 , 86.82, 88.11, 85.75, 87.31, 88.63, 84.24, 88.37, 86.27,
       88.6 , 86.56, 89.15, 83.72, 85.49, 87.56, 86.56, 88.11, 88.37,
       85.23, 87.31, 88.11, 87.86, 87.08, 87.82, 85.75, 84.75, 87.08,
       87.86, 87.31, 88.08, 87.6 , 88.11, 85.01, 85.49, 88.08, 87.34,
       86.56, 88.89, 86.53, 87.05, 87.08, 86.05, 85.53, 88.6 , 88.34,
       87.6 , 85.79, 87.34, 87.82, 86.79])
Mean   | Max    | Min
87.06% | 89.15% | 83.72%
ROC AUC score array: array([76.87, 73.51, 77.21, 73.18, 76.82, 77.91, 68.6 , 78.8 , 74.23,
       78.76, 74.76, 80.74, 67.91, 70.88, 75.91, 73.7 , 78.28, 77.38,
       70.71, 76.82, 77.21, 77.39, 75.81, 76.68, 72.55, 70.01, 75.1 ,
       76.33, 77.76, 76.97, 74.74, 77.56, 71.96, 73.01, 77.34, 77.05,
       73.34, 79.5 , 74.4 , 74.85, 75.46, 73.35, 70.53, 78.97, 77.87,
       76.51, 71.41, 76.7 , 78.1 , 74.68])
Mean   | Max    | Min
75.32% | 80.74% | 67.91%


In [30]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['logistic regression', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['logistic regression', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 5.2 Apply Logistic Regression with 5 K-Fold, X input: mean_final_concatenate

In [31]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [32]:
# Apply Logistic Regression with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # Logistic Regression
    LR = LogisticRegression(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    LR.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = LR.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 86.30%
ROC AUC score: 73.53%
RepeatedStratifiedKFold = 2
Accuracy: 86.30%
ROC AUC score: 72.82%
RepeatedStratifiedKFold = 3
Accuracy: 86.05%
ROC AUC score: 72.64%
RepeatedStratifiedKFold = 4
Accuracy: 84.97%
ROC AUC score: 71.60%
RepeatedStratifiedKFold = 5
Accuracy: 84.97%
ROC AUC score: 70.95%
RepeatedStratifiedKFold = 6
Accuracy: 86.05%
ROC AUC score: 73.35%
RepeatedStratifiedKFold = 7
Accuracy: 83.72%
ROC AUC score: 68.26%
RepeatedStratifiedKFold = 8
Accuracy: 86.82%
ROC AUC score: 74.22%
RepeatedStratifiedKFold = 9


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Accuracy: 84.72%
ROC AUC score: 70.01%
RepeatedStratifiedKFold = 10
Accuracy: 87.31%
ROC AUC score: 75.74%
RepeatedStratifiedKFold = 11
Accuracy: 86.56%
ROC AUC score: 73.70%
RepeatedStratifiedKFold = 12
Accuracy: 88.89%
ROC AUC score: 77.72%
RepeatedStratifiedKFold = 13
Accuracy: 82.69%
ROC AUC score: 67.22%
RepeatedStratifiedKFold = 14
Accuracy: 82.38%
ROC AUC score: 65.27%
RepeatedStratifiedKFold = 15
Accuracy: 86.27%
ROC AUC score: 73.25%
RepeatedStratifiedKFold = 16
Accuracy: 85.53%
ROC AUC score: 71.95%
RepeatedStratifiedKFold = 17
Accuracy: 86.05%
ROC AUC score: 73.71%


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


RepeatedStratifiedKFold = 18
Accuracy: 87.08%
ROC AUC score: 73.68%
RepeatedStratifiedKFold = 19
Accuracy: 82.64%
ROC AUC score: 66.51%
RepeatedStratifiedKFold = 20
Accuracy: 86.01%
ROC AUC score: 72.72%
RepeatedStratifiedKFold = 21
Accuracy: 84.75%
ROC AUC score: 71.43%
RepeatedStratifiedKFold = 22
Accuracy: 86.82%
ROC AUC score: 74.58%
RepeatedStratifiedKFold = 23
Accuracy: 86.05%
ROC AUC score: 72.64%
RepeatedStratifiedKFold = 24
Accuracy: 86.79%
ROC AUC score: 73.51%
RepeatedStratifiedKFold = 25
Accuracy: 84.20%
ROC AUC score: 69.36%
RepeatedStratifiedKFold = 26


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Accuracy: 83.72%
ROC AUC score: 68.97%
RepeatedStratifiedKFold = 27
Accuracy: 85.01%
ROC AUC score: 70.18%
RepeatedStratifiedKFold = 28
Accuracy: 85.53%
ROC AUC score: 72.30%
RepeatedStratifiedKFold = 29
Accuracy: 87.31%
ROC AUC score: 74.92%
RepeatedStratifiedKFold = 30
Accuracy: 87.05%
ROC AUC score: 75.21%
RepeatedStratifiedKFold = 31
Accuracy: 86.05%
ROC AUC score: 72.29%
RepeatedStratifiedKFold = 32
Accuracy: 87.34%
ROC AUC score: 74.92%
RepeatedStratifiedKFold = 33
Accuracy: 83.98%
ROC AUC score: 69.14%
RepeatedStratifiedKFold = 34
Accuracy: 83.16%
ROC AUC score: 67.92%
RepeatedStratifiedKFold = 35
Accuracy: 87.56%
ROC AUC score: 75.91%
RepeatedStratifiedKFold = 36
Accuracy: 84.50%
ROC AUC score: 70.91%
RepeatedStratifiedKFold = 37
Accuracy: 86.30%
ROC AUC score: 72.82%
RepeatedStratifiedKFold = 38
Accuracy: 87.08%
ROC AUC score: 74.75%
RepeatedStratifiedKFold = 39
Accuracy: 85.49%
ROC AUC score: 72.30%
RepeatedStratifiedKFold = 40
Accuracy: 85.75%
ROC AUC score: 71.83%
RepeatedS

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Accuracy: 87.82%
ROC AUC score: 75.97%
RepeatedStratifiedKFold = 45
Accuracy: 87.82%
ROC AUC score: 75.36%
RepeatedStratifiedKFold = 46
Accuracy: 86.30%
ROC AUC score: 72.46%
RepeatedStratifiedKFold = 47
Accuracy: 83.20%
ROC AUC score: 67.56%
RepeatedStratifiedKFold = 48
Accuracy: 85.53%
ROC AUC score: 71.59%
RepeatedStratifiedKFold = 49
Accuracy: 85.49%
ROC AUC score: 73.36%
RepeatedStratifiedKFold = 50
Accuracy: 86.53%
ROC AUC score: 73.78%


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [33]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([86.3 , 86.3 , 86.05, 84.97, 84.97, 86.05, 83.72, 86.82, 84.72,
       87.31, 86.56, 88.89, 82.69, 82.38, 86.27, 85.53, 86.05, 87.08,
       82.64, 86.01, 84.75, 86.82, 86.05, 86.79, 84.2 , 83.72, 85.01,
       85.53, 87.31, 87.05, 86.05, 87.34, 83.98, 83.16, 87.56, 84.5 ,
       86.3 , 87.08, 85.49, 85.75, 84.24, 84.5 , 85.01, 87.82, 87.82,
       86.3 , 83.2 , 85.53, 85.49, 86.53])
Mean   | Max    | Min
85.64% | 88.89% | 82.38%
ROC AUC score array: array([73.53, 72.82, 72.64, 71.6 , 70.95, 73.35, 68.26, 74.22, 70.01,
       75.74, 73.7 , 77.72, 67.22, 65.27, 73.25, 71.95, 73.71, 73.68,
       66.51, 72.72, 71.43, 74.58, 72.64, 73.51, 69.36, 68.97, 70.18,
       72.3 , 74.92, 75.21, 72.29, 74.92, 69.14, 67.92, 75.91, 70.91,
       72.82, 74.75, 72.3 , 71.83, 70.38, 70.2 , 70.54, 75.97, 75.36,
       72.46, 67.56, 71.59, 73.36, 73.78])
Mean   | Max    | Min
72.12% | 77.72% | 65.27%


In [34]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['logistic regression', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['logistic regression', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

# 6. Model 4: Support Vector Machine

### 6.1 Apply Support Vector Machine with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [35]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [36]:
# Apply Support Vector Machine with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # Support Vector Machine
    SVM = LinearSVC(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    SVM.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = SVM.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


RepeatedStratifiedKFold = 1
Accuracy: 86.56%
ROC AUC score: 72.99%
RepeatedStratifiedKFold = 2
Accuracy: 86.56%
ROC AUC score: 73.34%
RepeatedStratifiedKFold = 3


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


Accuracy: 86.05%
ROC AUC score: 72.64%
RepeatedStratifiedKFold = 4


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


...

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


Accuracy: 86.56%
ROC AUC score: 72.99%
RepeatedStratifiedKFold = 47
Accuracy: 83.46%
ROC AUC score: 67.38%
RepeatedStratifiedKFold = 48
Accuracy: 85.79%
ROC AUC score: 73.18%
RepeatedStratifiedKFold = 49


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


Accuracy: 89.12%
ROC AUC score: 78.96%
RepeatedStratifiedKFold = 50
Accuracy: 87.05%
ROC AUC score: 74.13%


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


In [37]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([86.56, 86.56, 86.05, 85.75, 86.01, 86.82, 83.98, 87.6 , 84.97,
       88.34, 88.37, 88.63, 83.98, 85.23, 86.01, 86.05, 87.34, 87.34,
       83.94, 86.53, 86.05, 86.82, 86.56, 85.75, 79.53, 83.98, 85.53,
       86.05, 86.79, 87.82, 87.34, 88.11, 85.27, 82.9 , 87.56, 85.53,
       88.11, 86.82, 85.49, 86.27, 86.82, 84.24, 85.53, 86.79, 87.31,
       86.56, 83.46, 85.79, 89.12, 87.05])
Mean   | Max    | Min
86.14% | 89.12% | 79.53%
ROC AUC score array: array([72.99, 73.34, 72.64, 72.47, 72.36, 74.58, 68.08, 75.8 , 69.83,
       76.79, 77.74, 77.55, 68.79, 70.35, 71.64, 72.64, 75.28, 74.92,
       67.72, 73.78, 73.  , 74.58, 73.34, 72.47, 67.36, 68.79, 71.59,
       72.29, 76.7 , 76.44, 74.57, 75.79, 71.42, 67.74, 75.91, 71.59,
       76.14, 74.58, 71.24, 72.53, 73.87, 68.96, 70.88, 74.58, 75.02,
       72.99, 67.38, 73.18, 78.96, 74.13])
Mean   | Max    | Min
72.95% | 78.96% | 67.36%


In [38]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['support vector machine', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['support vector machine', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 6.2 Apply Support Vector Machine with Repeated Stratified 5-Fold 10 times, X input: mean_final_concatenate

In [39]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [40]:
# Apply Support Vector Machine with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # Support Vector Machine
    SVM = LinearSVC(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    SVM.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = SVM.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 92.76%
ROC AUC score: 87.04%
RepeatedStratifiedKFold = 2
Accuracy: 94.06%
ROC AUC score: 89.67%
RepeatedStratifiedKFold = 3
Accuracy: 92.25%
ROC AUC score: 84.92%
RepeatedStratifiedKFold = 4


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


Accuracy: 90.16%
ROC AUC score: 83.90%
RepeatedStratifiedKFold = 5
Accuracy: 90.16%
ROC AUC score: 81.95%
RepeatedStratifiedKFold = 6
Accuracy: 92.25%
ROC AUC score: 85.99%
RepeatedStratifiedKFold = 7
Accuracy: 92.25%
ROC AUC score: 85.63%
RepeatedStratifiedKFold = 8


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


Accuracy: 91.99%
ROC AUC score: 85.10%
RepeatedStratifiedKFold = 9
Accuracy: 90.41%
ROC AUC score: 83.72%
RepeatedStratifiedKFold = 10
Accuracy: 92.75%
ROC AUC score: 87.27%
RepeatedStratifiedKFold = 11
Accuracy: 91.99%
ROC AUC score: 86.52%
RepeatedStratifiedKFold = 12
Accuracy: 92.25%
ROC AUC score: 85.63%
RepeatedStratifiedKFold = 13
Accuracy: 89.92%
ROC AUC score: 82.67%
RepeatedStratifiedKFold = 14
Accuracy: 90.93%
ROC AUC score: 83.35%
RepeatedStratifiedKFold = 15
Accuracy: 93.52%
ROC AUC score: 88.14%
RepeatedStratifiedKFold = 16
Accuracy: 90.44%
ROC AUC score: 82.66%
RepeatedStratifiedKFold = 17
Accuracy: 90.96%
ROC AUC score: 84.42%
RepeatedStratifiedKFold = 18
Accuracy: 92.76%
ROC AUC score: 87.04%
RepeatedStratifiedKFold = 19


...

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


Accuracy: 93.78%
ROC AUC score: 89.14%
RepeatedStratifiedKFold = 45
Accuracy: 91.71%
ROC AUC score: 85.50%
RepeatedStratifiedKFold = 46
Accuracy: 92.51%
ROC AUC score: 85.80%
RepeatedStratifiedKFold = 47


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


Accuracy: 93.54%
ROC AUC score: 88.26%
RepeatedStratifiedKFold = 48
Accuracy: 89.41%
ROC AUC score: 81.26%
RepeatedStratifiedKFold = 49
Accuracy: 91.97%
ROC AUC score: 86.17%
RepeatedStratifiedKFold = 50
Accuracy: 92.23%
ROC AUC score: 85.85%


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/svm/_base.py:985: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn("Liblinear failed to converge, increase "


In [41]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([92.76, 94.06, 92.25, 90.16, 90.16, 92.25, 92.25, 91.99, 90.41,
       92.75, 91.99, 92.25, 89.92, 90.93, 93.52, 90.44, 90.96, 92.76,
       92.75, 92.75, 92.25, 91.73, 92.25, 91.45, 91.71, 91.47, 92.25,
       91.99, 91.97, 91.71, 93.54, 92.76, 90.44, 89.38, 93.01, 89.66,
       94.57, 91.73, 91.97, 91.97, 90.18, 90.44, 93.28, 93.78, 91.71,
       92.51, 93.54, 89.41, 91.97, 92.23])
Mean   | Max    | Min
91.88% | 94.57% | 89.38%
ROC AUC score array: array([87.04, 89.67, 84.92, 83.9 , 81.95, 85.99, 85.63, 85.1 , 83.72,
       87.27, 86.52, 85.63, 82.67, 83.35, 88.14, 82.66, 84.42, 87.04,
       87.04, 86.55, 86.7 , 85.64, 84.92, 84.76, 85.5 , 85.47, 85.99,
       85.46, 84.75, 85.86, 87.55, 86.68, 83.72, 80.55, 88.88, 81.79,
       90.37, 84.22, 86.17, 85.31, 82.13, 82.3 , 88.45, 89.14, 85.5 ,
       85.8 , 88.26, 81.26, 86.17, 85.85])
Mean   | Max    | Min
85.49% | 90.37% | 80.55%


In [42]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['support vector machine', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['support vector machine', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

# 7. Model 5: MLP Classifier

### 7.1 Apply MLP Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [43]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [44]:
# Apply MLP Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # MLP Classifier
    MLP = MLPClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    MLP.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = MLP.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 87.60%
ROC AUC score: 76.51%
RepeatedStratifiedKFold = 2
Accuracy: 76.74%
ROC AUC score: 69.32%
RepeatedStratifiedKFold = 3


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Accuracy: 86.56%
ROC AUC score: 72.63%
RepeatedStratifiedKFold = 4
Accuracy: 74.87%
ROC AUC score: 68.09%
RepeatedStratifiedKFold = 5
Accuracy: 84.72%
ROC AUC score: 69.70%
RepeatedStratifiedKFold = 6


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Accuracy: 88.37%
ROC AUC score: 77.38%
RepeatedStratifiedKFold = 7


...

Accuracy: 75.71%
ROC AUC score: 67.22%
RepeatedStratifiedKFold = 48


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Accuracy: 88.11%
ROC AUC score: 77.21%
RepeatedStratifiedKFold = 49


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Accuracy: 74.09%
ROC AUC score: 68.99%
RepeatedStratifiedKFold = 50
Accuracy: 83.94%
ROC AUC score: 67.74%


In [45]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([87.6 , 76.74, 86.56, 74.87, 84.72, 88.37, 84.75, 88.89, 79.02,
       81.87, 86.82, 77.78, 73.64, 76.68, 73.06, 83.72, 76.23, 86.82,
       85.75, 87.56, 87.86, 76.74, 81.4 , 76.17, 85.75, 86.56, 82.69,
       75.97, 75.65, 86.01, 76.74, 85.01, 73.64, 78.76, 84.97, 87.08,
       73.13, 88.63, 72.02, 87.05, 87.34, 86.82, 84.75, 75.39, 87.56,
       82.17, 75.71, 88.11, 74.09, 83.94])
Mean   | Max    | Min
81.78% | 88.89% | 72.02%
ROC AUC score array: array([76.51, 69.32, 72.63, 68.09, 69.7 , 77.38, 70.01, 79.14, 70.13,
       62.77, 74.93, 73.56, 66.2 , 69.65, 67.04, 66.84, 71.46, 73.51,
       72.47, 76.99, 77.04, 70.39, 72.05, 70.01, 72.19, 73.34, 65.09,
       70.94, 70.02, 72.  , 72.16, 69.83, 66.91, 69.6 , 69.51, 76.88,
       65.5 , 78.26, 66.2 , 74.85, 75.63, 74.22, 69.3 , 70.56, 74.83,
       72.92, 67.22, 77.21, 68.99, 67.74])
Mean   | Max    | Min
71.39% | 79.14% | 62.77%


In [46]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['mlp', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['mlp', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 7.2 Apply MLP Classifier with Repeated Stratified 5-Fold 10 times X input: mean_final_concatenate

In [47]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [48]:
# Apply MLP Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # MLP Classifier
    MLP = MLPClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    MLP.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = MLP.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 88.11%
ROC AUC score: 76.14%
RepeatedStratifiedKFold = 2


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Accuracy: 80.10%
ROC AUC score: 71.55%
RepeatedStratifiedKFold = 3


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Accuracy: 81.65%
ROC AUC score: 70.80%
RepeatedStratifiedKFold = 4
Accuracy: 86.01%
ROC AUC score: 72.64%
RepeatedStratifiedKFold = 5
Accuracy: 83.94%
ROC AUC score: 67.74%
RepeatedStratifiedKFold = 6


...

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Accuracy: 86.05%
ROC AUC score: 73.00%
RepeatedStratifiedKFold = 49


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Accuracy: 79.79%
ROC AUC score: 71.71%
RepeatedStratifiedKFold = 50
Accuracy: 88.08%
ROC AUC score: 75.89%


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/sklearn/neural_network/_multilayer_perceptron.py:614: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


In [49]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([88.11, 80.1 , 81.65, 86.01, 83.94, 88.11, 84.5 , 87.34, 81.61,
       88.86, 86.05, 82.17, 83.72, 83.16, 85.75, 85.79, 80.62, 85.01,
       86.01, 78.76, 86.56, 81.91, 86.82, 86.01, 86.27, 85.01, 85.79,
       79.33, 80.31, 80.05, 86.05, 82.17, 85.53, 77.98, 80.05, 85.79,
       83.72, 87.86, 87.05, 86.27, 71.58, 79.59, 82.95, 87.82, 86.53,
       77.  , 74.42, 86.05, 79.79, 88.08])
Mean   | Max    | Min
83.63% | 88.86% | 71.58%
ROC AUC score array: array([76.14, 71.55, 70.8 , 72.64, 67.74, 75.79, 69.49, 75.28, 82.84,
       78.21, 73.35, 80.37, 67.55, 65.79, 70.74, 71.41, 78.99, 69.47,
       71.93, 69.01, 73.34, 80.91, 73.51, 71.93, 71.81, 70.18, 71.41,
       77.42, 77.72, 81.04, 71.58, 83.92, 71.24, 66.61, 71.31, 72.47,
       67.2 , 75.26, 74.39, 72.89, 64.83, 68.72, 81.95, 75.62, 72.7 ,
       75.53, 64.58, 73.  , 71.71, 75.89])
Mean   | Max    | Min
73.20% | 83.92% | 64.58%


In [50]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['mlp', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['mlp', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

# 8. Model 6: XGBoost Classifier

### 8.1 Apply XGBoost Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [51]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [52]:
# Apply XGBoost Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # XGBoost Classifier
    XGB = XGBClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    XGB.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = XGB.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


RepeatedStratifiedKFold = 1
[13:49:27] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Accuracy: 95.09%
ROC AUC score: 92.84%
RepeatedStratifiedKFold = 2
[13:49:27] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Accuracy: 95.61%
ROC AUC score: 93.89%
RepeatedStratifiedKFold = 3
[13:49:28] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logist

/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


Accuracy: 97.16%
ROC AUC score: 95.63%
RepeatedStratifiedKFold = 4
[13:49:28] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Accuracy: 93.26%
ROC AUC score: 90.57%
RepeatedStratifiedKFold = 5
[13:49:28] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


...

Accuracy: 95.61%
ROC AUC score: 94.60%
RepeatedStratifiedKFold = 47
[13:49:34] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Accuracy: 95.35%
ROC AUC score: 92.66%
RepeatedStratifiedKFold = 48
[13:49:34] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


Accuracy: 96.12%
ROC AUC score: 94.59%
RepeatedStratifiedKFold = 49
[13:49:34] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Accuracy: 95.34%
ROC AUC score: 94.43%
RepeatedStratifiedKFold = 50
[13:49:34] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


Accuracy: 95.85%
ROC AUC score: 93.29%


In [53]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([95.09, 95.61, 97.16, 93.26, 94.82, 96.64, 95.61, 94.57, 96.11,
       96.37, 96.12, 95.61, 94.32, 96.37, 96.11, 94.32, 95.09, 96.64,
       95.08, 95.85, 95.87, 95.87, 95.35, 94.56, 96.11, 94.32, 95.35,
       96.38, 95.6 , 95.34, 97.67, 95.09, 94.83, 95.6 , 95.85, 93.8 ,
       96.9 , 96.12, 96.11, 96.11, 95.61, 95.09, 96.9 , 96.37, 94.3 ,
       95.61, 95.35, 96.12, 95.34, 95.85])
Mean   | Max    | Min
95.60% | 97.67% | 93.26%
ROC AUC score array: array([92.84, 93.89, 95.63, 90.57, 94.05, 94.93, 92.83, 92.85, 94.94,
       96.52, 95.3 , 94.6 , 92.33, 93.7 , 94.55, 91.26, 93.55, 95.29,
       92.84, 94.74, 94.42, 94.77, 94.08, 92.85, 94.19, 92.33, 94.43,
       94.41, 94.24, 93.67, 96.68, 94.26, 92.31, 93.18, 94.74, 92.34,
       96.17, 94.24, 94.23, 94.55, 94.25, 92.84, 96.17, 96.18, 91.18,
       94.6 , 92.66, 94.59, 94.43, 93.29])
Mean   | Max    | Min
93.99% | 96.68% | 90.57%


In [54]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['xgboost', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['xgboost', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 8.2 Apply XGBoost Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_concatenate

In [55]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [56]:
# Apply XGBoost Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # XGBoost Classifier
    XGB = XGBClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    XGB.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = XGB.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
[13:49:34] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


Accuracy: 95.61%
ROC AUC score: 93.89%
RepeatedStratifiedKFold = 2
[13:49:35] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Accuracy: 95.61%
ROC AUC score: 93.89%
RepeatedStratifiedKFold = 3
[13:49:35] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


Accuracy: 97.16%
ROC AUC score: 95.99%
RepeatedStratifiedKFold = 4
[13:49:35] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


...

Accuracy: 95.87%
ROC AUC score: 94.06%
RepeatedStratifiedKFold = 48
[13:49:44] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Accuracy: 96.12%
ROC AUC score: 94.95%
RepeatedStratifiedKFold = 49
[13:49:45] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)
/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


Accuracy: 95.08%
ROC AUC score: 94.25%
RepeatedStratifiedKFold = 50
[13:49:45] WARNING: /Users/runner/miniforge3/conda-bld/xgboost-split_1637426408905/work/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


/Users/Joshua/opt/anaconda3/lib/python3.8/site-packages/xgboost/sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


Accuracy: 96.37%
ROC AUC score: 94.00%


In [57]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([95.61, 95.61, 97.16, 94.56, 95.85, 95.87, 95.35, 95.35, 96.11,
       96.37, 96.38, 95.61, 95.09, 95.08, 96.37, 94.83, 95.35, 96.64,
       96.11, 95.34, 96.38, 95.35, 95.09, 94.56, 95.6 , 94.06, 95.61,
       96.9 , 95.85, 95.85, 97.16, 95.61, 95.35, 95.6 , 95.85, 94.06,
       97.42, 95.09, 96.37, 95.85, 95.61, 94.57, 97.16, 96.11, 94.3 ,
       95.87, 95.87, 96.12, 95.08, 96.37])
Mean   | Max    | Min
95.71% | 97.42% | 94.06%
ROC AUC score array: array([93.89, 93.89, 95.99, 93.2 , 95.1 , 93.71, 92.3 , 93.72, 95.3 ,
       96.16, 95.83, 94.6 , 92.84, 91.77, 94.72, 91.96, 94.08, 95.29,
       94.59, 94.03, 95.12, 93.72, 93.55, 93.2 , 93.48, 92.51, 94.6 ,
       94.75, 95.12, 94.74, 95.99, 94.25, 93.01, 93.53, 94.74, 92.87,
       96.51, 92.84, 95.47, 93.65, 94.25, 92.14, 96.34, 95.65, 91.18,
       94.42, 94.06, 94.95, 94.25, 94.  ])
Mean   | Max    | Min
94.16% | 96.51% | 91.18%


In [58]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['xgboost', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['xgboost', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

# 9. Model 7: LightGBM Classifier

### 9.1 Apply LightGBM Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [59]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [60]:
# Apply LightGBM Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # LightGBM Classifier
    lgbm = LGBMClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    lgbm.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = lgbm.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 95.87%
ROC AUC score: 94.42%
RepeatedStratifiedKFold = 2
Accuracy: 95.87%
ROC AUC score: 94.06%
RepeatedStratifiedKFold = 3
Accuracy: 97.16%
ROC AUC score: 95.63%
RepeatedStratifiedKFold = 4
Accuracy: 93.78%
ROC AUC score: 91.27%
RepeatedStratifiedKFold = 5
Accuracy: 95.08%
ROC AUC score: 94.22%
RepeatedStratifiedKFold = 6
Accuracy: 95.87%
ROC AUC score: 93.71%
RepeatedStratifiedKFold = 7
Accuracy: 95.35%
ROC AUC score: 92.66%
RepeatedStratifiedKFold = 8
Accuracy: 94.57%
ROC AUC score: 92.85%
RepeatedStratifiedKFold = 9
Accuracy: 96.11%
ROC AUC score: 94.94%
RepeatedStratifiedKFold = 10
Accuracy: 96.37%
ROC AUC score: 96.52%
RepeatedStratifiedKFold = 11
Accuracy: 96.12%
ROC AUC score: 95.30%
RepeatedStratifiedKFold = 12
Accuracy: 95.61%
ROC AUC score: 94.60%
RepeatedStratifiedKFold = 13
Accuracy: 95.35%
ROC AUC score: 93.72%
RepeatedStratifiedKFold = 14
Accuracy: 94.82%
ROC AUC score: 91.60%
RepeatedStratifiedKFold = 15
Accuracy: 95.34%
ROC AUC sco

In [61]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([95.87, 95.87, 97.16, 93.78, 95.08, 95.87, 95.35, 94.57, 96.11,
       96.37, 96.12, 95.61, 95.35, 94.82, 95.34, 94.57, 95.09, 96.64,
       94.82, 95.34, 95.87, 96.12, 94.83, 94.82, 96.63, 94.06, 95.61,
       95.87, 95.85, 95.6 , 97.67, 95.35, 94.83, 95.34, 95.85, 93.28,
       96.64, 96.12, 96.11, 95.85, 95.87, 95.35, 97.16, 96.37, 94.3 ,
       95.87, 95.61, 96.38, 95.34, 96.11])
Mean   | Max    | Min
95.61% | 97.67% | 93.28%
ROC AUC score array: array([94.42, 94.06, 95.63, 91.27, 94.22, 93.71, 92.66, 92.85, 94.94,
       96.52, 95.3 , 94.6 , 93.72, 91.6 , 92.95, 91.79, 93.55, 94.93,
       92.66, 94.03, 94.42, 94.95, 93.38, 93.37, 94.17, 92.16, 94.6 ,
       93.35, 94.77, 94.2 , 96.68, 94.43, 92.31, 92.65, 94.74, 91.29,
       95.64, 94.24, 94.59, 93.29, 94.77, 93.37, 96.34, 95.82, 91.18,
       94.77, 93.18, 95.12, 94.43, 93.82])
Mean   | Max    | Min
93.95% | 96.68% | 91.18%


In [62]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['lightgbm', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['lightgbm', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 9.2 Apply LightGBM Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_concatenate

In [63]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [64]:
# Apply LightGBM Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # LightGBM Classifier
    lgbm = LGBMClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    lgbm.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = lgbm.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Accuracy: 95.61%
ROC AUC score: 93.89%
RepeatedStratifiedKFold = 2
Accuracy: 95.87%
ROC AUC score: 94.06%
RepeatedStratifiedKFold = 3
Accuracy: 97.16%
ROC AUC score: 95.99%
RepeatedStratifiedKFold = 4
Accuracy: 94.56%
ROC AUC score: 93.20%
RepeatedStratifiedKFold = 5
Accuracy: 95.60%
ROC AUC score: 94.92%
RepeatedStratifiedKFold = 6
Accuracy: 96.38%
ROC AUC score: 94.41%
RepeatedStratifiedKFold = 7
Accuracy: 95.61%
ROC AUC score: 92.83%
RepeatedStratifiedKFold = 8
Accuracy: 95.35%
ROC AUC score: 93.72%
RepeatedStratifiedKFold = 9
Accuracy: 96.11%
ROC AUC score: 95.30%
RepeatedStratifiedKFold = 10
Accuracy: 96.37%
ROC AUC score: 96.16%
RepeatedStratifiedKFold = 11
Accuracy: 96.12%
ROC AUC score: 95.66%
RepeatedStratifiedKFold = 12
Accuracy: 95.61%
ROC AUC score: 94.60%
RepeatedStratifiedKFold = 13
Accuracy: 95.87%
ROC AUC score: 94.77%
RepeatedStratifiedKFold = 14
Accuracy: 95.60%
ROC AUC score: 92.47%
RepeatedStratifiedKFold = 15
Accuracy: 96.37%
ROC AUC sco

In [65]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([95.61, 95.87, 97.16, 94.56, 95.6 , 96.38, 95.61, 95.35, 96.11,
       96.37, 96.12, 95.61, 95.87, 95.6 , 96.37, 95.09, 94.83, 96.38,
       95.6 , 95.34, 96.38, 96.12, 94.83, 94.82, 95.85, 94.57, 95.09,
       96.64, 96.11, 96.11, 97.42, 95.87, 95.35, 95.34, 95.85, 93.8 ,
       97.16, 95.61, 96.89, 96.89, 96.12, 94.57, 97.16, 96.11, 94.3 ,
       95.87, 96.38, 96.12, 95.34, 96.63])
Mean   | Max    | Min
95.81% | 97.42% | 93.80%
ROC AUC score array: array([93.89, 94.06, 95.99, 93.2 , 94.92, 94.41, 92.83, 93.72, 95.3 ,
       96.16, 95.66, 94.6 , 94.77, 92.47, 94.72, 92.84, 93.02, 95.12,
       94.24, 94.03, 95.12, 95.3 , 93.02, 93.73, 93.65, 92.85, 94.26,
       94.22, 95.3 , 94.91, 96.16, 94.77, 93.01, 93.36, 94.74, 92.34,
       96.34, 93.18, 95.81, 95.42, 94.95, 92.14, 96.34, 96.  , 91.18,
       94.42, 94.76, 94.95, 94.43, 94.53])
Mean   | Max    | Min
94.34% | 96.34% | 91.18%


In [66]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['lightgbm', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['lightgbm', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

# 10. Model 8: CatBoost Classifier

### 10.1 Apply CatBoost Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [67]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [68]:
# Apply CatBoost Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # CatBoost Classifier
    cat = CatBoostClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    cat.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = cat.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Learning rate set to 0.012409
0:	learn: 0.6755039	total: 62.2ms	remaining: 1m 2s
1:	learn: 0.6589370	total: 64.8ms	remaining: 32.3s
2:	learn: 0.6446223	total: 67ms	remaining: 22.3s
3:	learn: 0.6317577	total: 69.5ms	remaining: 17.3s
4:	learn: 0.6203447	total: 71.7ms	remaining: 14.3s
5:	learn: 0.6076009	total: 74ms	remaining: 12.3s
6:	learn: 0.5945697	total: 76.4ms	remaining: 10.8s
7:	learn: 0.5815274	total: 78.2ms	remaining: 9.69s
8:	learn: 0.5679648	total: 79.9ms	remaining: 8.8s
9:	learn: 0.5559642	total: 81.6ms	remaining: 8.08s
10:	learn: 0.5452977	total: 83.5ms	remaining: 7.51s
11:	learn: 0.5338324	total: 84.8ms	remaining: 6.98s
12:	learn: 0.5213392	total: 86.2ms	remaining: 6.54s
13:	learn: 0.5112795	total: 87.6ms	remaining: 6.17s
14:	learn: 0.5013731	total: 89.3ms	remaining: 5.86s
15:	learn: 0.4926867	total: 91.5ms	remaining: 5.63s
16:	learn: 0.4805535	total: 93.7ms	remaining: 5.42s
17:	learn: 0.4719075	total: 95.1ms	remaining: 5.19s
18:	learn: 0.4626510	

In [69]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([95.87, 95.87, 97.16, 93.52, 94.82, 96.38, 95.09, 95.09, 96.11,
       96.37, 95.87, 95.35, 95.61, 96.11, 95.85, 94.83, 95.09, 96.64,
       95.08, 95.34, 95.61, 96.38, 94.83, 94.56, 96.11, 94.57, 95.61,
       96.38, 95.6 , 96.11, 97.42, 96.12, 94.57, 95.6 , 95.6 , 93.28,
       96.64, 95.35, 96.89, 96.11, 95.61, 95.35, 96.64, 96.37, 94.56,
       95.61, 96.12, 96.12, 95.08, 96.37])
Mean   | Max    | Min
95.66% | 97.42% | 93.28%
ROC AUC score array: array([94.42, 94.06, 95.63, 91.1 , 94.05, 94.41, 92.49, 93.2 , 95.3 ,
       96.52, 94.77, 94.08, 93.89, 93.17, 94.37, 92.31, 93.55, 94.93,
       92.84, 93.67, 94.25, 95.47, 93.73, 92.85, 94.19, 92.5 , 94.6 ,
       94.41, 94.24, 94.55, 96.51, 94.95, 91.79, 93.18, 94.2 , 91.29,
       95.64, 93.01, 95.81, 94.55, 94.25, 93.37, 96.  , 95.82, 91.72,
       94.6 , 94.24, 94.59, 93.9 , 94.  ])
Mean   | Max    | Min
94.06% | 96.52% | 91.10%


In [70]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['catboost', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['catboost', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 10.2 Apply CatBoost Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_concatenate

In [71]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [72]:
# Apply CatBoost Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # CatBoost Classifier
    cat = CatBoostClassifier(random_state = 1001) # change the classifier here
    
    # Model fitting and training
    cat.fit(X_train, y_train)
    
    # Make predictions for validation data
    y_pred = cat.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Learning rate set to 0.012409
0:	learn: 0.6773484	total: 1.37ms	remaining: 1.37s
1:	learn: 0.6614163	total: 3.19ms	remaining: 1.59s
2:	learn: 0.6457974	total: 5.07ms	remaining: 1.68s
3:	learn: 0.6306846	total: 6.58ms	remaining: 1.64s
4:	learn: 0.6156159	total: 8.16ms	remaining: 1.62s
5:	learn: 0.5988544	total: 9.71ms	remaining: 1.61s
6:	learn: 0.5880341	total: 11.1ms	remaining: 1.58s
7:	learn: 0.5762368	total: 13ms	remaining: 1.61s
8:	learn: 0.5639438	total: 14.5ms	remaining: 1.59s
9:	learn: 0.5525256	total: 15.8ms	remaining: 1.57s
10:	learn: 0.5418832	total: 17.2ms	remaining: 1.55s
11:	learn: 0.5320653	total: 18.7ms	remaining: 1.54s
12:	learn: 0.5205561	total: 20.3ms	remaining: 1.54s
13:	learn: 0.5071011	total: 21.5ms	remaining: 1.51s
14:	learn: 0.4980961	total: 22.9ms	remaining: 1.5s
15:	learn: 0.4897012	total: 24.2ms	remaining: 1.49s
16:	learn: 0.4797751	total: 25.8ms	remaining: 1.49s
17:	learn: 0.4707111	total: 27.4ms	remaining: 1.49s
18:	learn: 0.462199

In [73]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([95.61, 96.12, 97.42, 94.56, 95.85, 96.38, 95.87, 95.09, 96.11,
       96.89, 96.38, 95.61, 95.61, 96.11, 96.37, 95.61, 95.35, 96.9 ,
       96.11, 95.34, 96.38, 96.38, 94.83, 94.82, 96.37, 94.83, 95.61,
       97.16, 95.85, 95.85, 97.67, 95.87, 95.61, 95.85, 95.85, 93.8 ,
       97.16, 95.87, 96.89, 95.6 , 96.38, 95.61, 96.64, 96.37, 94.3 ,
       95.87, 96.38, 96.38, 95.6 , 96.63])
Mean   | Max    | Min
95.95% | 97.67% | 93.80%
ROC AUC score array: array([93.89, 94.59, 96.16, 93.2 , 95.1 , 94.41, 93.  , 93.55, 95.3 ,
       96.86, 95.83, 94.6 , 94.25, 93.52, 94.72, 93.54, 94.08, 95.46,
       94.59, 93.67, 95.12, 95.47, 94.09, 93.37, 94.36, 93.02, 94.6 ,
       95.28, 94.77, 94.37, 96.68, 94.77, 93.54, 93.71, 94.74, 92.34,
       96.34, 93.35, 95.81, 93.12, 95.47, 93.89, 96.  , 96.18, 91.18,
       94.42, 94.76, 95.12, 94.95, 94.53])
Mean   | Max    | Min
94.51% | 96.86% | 91.18%


In [74]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['catboost', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['catboost', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

# 11. Model 9: TabNet Classifier

### 11.1 Apply TabNet Classifier with Repeated Stratified 5-Fold 10 times, X input: mean_final_elementwise_sum

In [75]:
# Classifying X and Y
X = mean_final_elementwise_sum
# X = mean_final_concatenate
y = IC50_class

In [76]:
# Apply TabNet Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # TabNet Classifier
    tn = TabNetClassifier(seed = 1001) # change the classifier here
    
    # Model fitting and training
    tn.fit(X_train, y_train, eval_set=[(X_validate, y_validate)])
    
    # Make predictions for validation data
    y_pred = tn.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Device used : cpu
epoch 0  | loss: 2.42371 | val_0_auc: 0.44052 |  0:00:00s
epoch 1  | loss: 1.23695 | val_0_auc: 0.57358 |  0:00:00s
epoch 2  | loss: 0.79659 | val_0_auc: 0.38742 |  0:00:00s
epoch 3  | loss: 0.61583 | val_0_auc: 0.66691 |  0:00:00s
epoch 4  | loss: 0.5125  | val_0_auc: 0.61417 |  0:00:01s
epoch 5  | loss: 0.39575 | val_0_auc: 0.57094 |  0:00:01s
epoch 6  | loss: 0.33403 | val_0_auc: 0.56269 |  0:00:01s
epoch 7  | loss: 0.33621 | val_0_auc: 0.52725 |  0:00:01s
epoch 8  | loss: 0.30935 | val_0_auc: 0.47585 |  0:00:01s
epoch 9  | loss: 0.26513 | val_0_auc: 0.52076 |  0:00:02s
epoch 10 | loss: 0.27161 | val_0_auc: 0.53861 |  0:00:02s
epoch 11 | loss: 0.26599 | val_0_auc: 0.31579 |  0:00:02s
epoch 12 | loss: 0.26764 | val_0_auc: 0.31424 |  0:00:02s
epoch 13 | loss: 0.25057 | val_0_auc: 0.31972 |  0:00:02s

Early stopping occured at epoch 13 with best_epoch = 3 and best_val_0_auc = 0.66691
Best weights from best epoch are automatically used!
Accu

In [77]:
# Printing Accuracy score and ROC AUC score
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([62.53, 75.45, 75.45, 72.54, 76.42, 24.55, 75.45, 75.45, 74.87,
       75.65, 75.45, 75.45, 75.45, 75.39, 68.39, 75.45, 24.55, 77.78,
       75.39, 44.56, 42.89, 75.45, 75.45, 49.22, 24.35, 75.45, 48.58,
       47.29, 74.87, 75.65, 75.45, 75.45, 24.55, 26.17, 75.65, 75.45,
       75.45, 73.64, 24.61, 75.65, 75.45, 75.45, 76.49, 75.39, 75.65,
       75.45, 77.78, 75.45, 75.39, 75.65])
Mean   | Max    | Min
66.11% | 77.78% | 24.35%
ROC AUC score array: array([63.45, 50.  , 64.56, 64.77, 79.73, 49.64, 50.  , 50.  , 49.66,
       50.  , 50.  , 50.  , 50.  , 50.  , 60.71, 50.  , 50.  , 82.08,
       50.  , 61.91, 61.09, 50.  , 50.  , 65.61, 50.  , 50.  , 63.44,
       63.65, 49.66, 50.  , 50.  , 50.  , 50.  , 50.68, 50.  , 50.  ,
       50.  , 67.62, 50.  , 50.  , 50.  , 50.  , 56.37, 50.  , 50.  ,
       50.  , 55.8 , 50.  , 50.  , 50.  ])
Mean   | Max    | Min
54.21% | 82.08% | 49.64%


In [78]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['tabnet', 'elementwise sum', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['tabnet', 'elementwise sum', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()

### 11.2 Apply TabNet Classifier with Repeated Stratified 5-Fold 10 timesd, X input: mean_final_concatenate

In [79]:
# Classifying X and Y
# X = mean_final_elementwise_sum
X = mean_final_concatenate
y = IC50_class

In [80]:
# Apply TabNet Classifier with Repeated Stratified 5-Fold 10 times
kf = RepeatedStratifiedKFold(n_splits=5, n_repeats=10, random_state = 1001)
# kf = StratifiedKFold(n_splits=5, random_state = 1001)
# kf = KFold(n_splits=5, randon_state = 1001)

accuracy_arr = []
roc_arr = []

i = 0
for train_index, validate_index in kf.split(X, y):
    i += 1
    print("RepeatedStratifiedKFold = " + str(i))
    
    # Split the training and validation dataset
    X_train, X_validate = X[train_index], X[validate_index]
    y_train, y_validate = y[train_index], y[validate_index]
    
    # TabNet Classifier
    tn = TabNetClassifier(seed = 1001) # change the classifier here
    
    # Model fitting and training
    tn.fit(X_train, y_train, eval_set=[(X_validate, y_validate)])
    
    # Make predictions for validation data
    y_pred = tn.predict(X_validate)
    predictions = [round(value) for value in y_pred]
    
    # Evaluate predictions: Accuracy score
    accuracy = accuracy_score(y_validate, predictions) * 100 # y_validate must match exactly with predictions in order to score accuracy points
    accuracy_arr.append(accuracy)
    print("Accuracy: %.2f%%" % (accuracy))
    
    # Evaluate predictions: ROC AUC score
    roc_score = roc_auc_score(y_validate, predictions) * 100
    roc_arr.append(roc_score)
    print("ROC AUC score: %.2f%%" % (roc_score))
    
    # # Evaluate predictions: Classification report
    # cr = classification_report(y_validate, predictions)
    # print("Classification report:")
    # print(cr)
    
    # # Evaluate predictions: Confusion Matrix
    # cm = confusion_matrix(y_validate, predictions)
    # print("Confusion matrix:")
    # print(cm)
    
    print("=" * 30)

accuracy_arr = np.asarray(accuracy_arr)
roc_arr = np.asarray(roc_arr)

RepeatedStratifiedKFold = 1
Device used : cpu
epoch 0  | loss: 0.67013 | val_0_auc: 0.14618 |  0:00:00s
epoch 1  | loss: 0.55141 | val_0_auc: 0.52686 |  0:00:00s
epoch 2  | loss: 0.49309 | val_0_auc: 0.59005 |  0:00:00s
epoch 3  | loss: 0.45272 | val_0_auc: 0.47235 |  0:00:00s
epoch 4  | loss: 0.45132 | val_0_auc: 0.66741 |  0:00:01s
epoch 5  | loss: 0.44489 | val_0_auc: 0.83832 |  0:00:01s
epoch 6  | loss: 0.40974 | val_0_auc: 0.79211 |  0:00:01s
epoch 7  | loss: 0.39901 | val_0_auc: 0.23569 |  0:00:01s
epoch 8  | loss: 0.35104 | val_0_auc: 0.23983 |  0:00:01s
epoch 9  | loss: 0.31865 | val_0_auc: 0.30458 |  0:00:01s
epoch 10 | loss: 0.28981 | val_0_auc: 0.19946 |  0:00:02s
epoch 11 | loss: 0.27619 | val_0_auc: 0.26136 |  0:00:02s
epoch 12 | loss: 0.26928 | val_0_auc: 0.20883 |  0:00:02s
epoch 13 | loss: 0.22363 | val_0_auc: 0.69131 |  0:00:02s
epoch 14 | loss: 0.2145  | val_0_auc: 0.71013 |  0:00:02s
epoch 15 | loss: 0.21781 | val_0_auc: 0.68868 |  0:00:03s

Early stopping occured at

In [81]:
mean_acc = np.mean(accuracy_arr)
max_acc = np.max(accuracy_arr)
min_acc = np.min(accuracy_arr)

mean_roc = np.mean(roc_arr)
max_roc = np.max(roc_arr)
min_roc = np.min(roc_arr)

print("Accuracy score array: " + repr(np.round(accuracy_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_acc, max_acc, min_acc))
print("ROC AUC score array: " + repr(np.round(roc_arr, 2)))
print("Mean   | Max    | Min")
print("%.2f%% | %.2f%% | %.2f%%" % (mean_roc, max_roc, min_roc))

Accuracy score array: array([75.45, 82.69, 75.45, 75.39, 75.65, 75.45, 75.45, 75.45, 75.39,
       75.65, 75.45, 75.45, 68.73, 75.39, 75.65, 75.45, 75.45, 75.45,
       75.39, 67.1 , 78.04, 75.45, 75.45, 75.65, 75.65, 75.45, 75.45,
       75.45, 74.61, 75.65, 75.45, 75.45, 67.18, 78.24, 75.65, 75.45,
       75.45, 79.07, 75.39, 75.65, 75.45, 75.45, 72.87, 75.39, 75.65,
       75.45, 75.45, 75.45, 75.39, 75.65])
Mean   | Max    | Min
75.27% | 82.69% | 67.10%
ROC AUC score array: array([50.  , 69.35, 50.  , 50.  , 50.  , 50.  , 50.  , 50.  , 50.  ,
       50.  , 50.  , 50.  , 64.01, 50.  , 50.  , 50.  , 50.  , 50.  ,
       50.  , 60.58, 81.18, 50.  , 50.  , 50.53, 50.  , 50.  , 50.  ,
       50.  , 50.19, 50.  , 50.  , 50.  , 59.08, 69.97, 50.  , 50.  ,
       50.  , 80.8 , 50.  , 50.  , 50.  , 50.  , 78.11, 50.  , 50.  ,
       50.  , 50.  , 50.  , 50.  , 50.  ])
Mean   | Max    | Min
53.28% | 81.18% | 50.00%


In [82]:
# Open your CSV file in append mode
# Create a file object for this file

with open(csv_file_name, 'a+', newline = '') as f_object:
    
    writer_object = csv.writer(f_object)
    writer_object.writerow(['tabnet', 'concatenate', 'accuracy'] + [mean_acc, max_acc, min_acc] + accuracy_arr.tolist())
    writer_object.writerow(['tabnet', 'concatenate', 'roc auc'] + [mean_roc, max_roc, min_roc] + roc_arr.tolist())

    #Close the file object
    f_object.close()